## Gradient Descent, Gradient Boosting i Sieci Neuronowe
Czyli sprint po podwalinach obecnego state-of-the-art w uczeniu maszynowym

In [309]:
import pandas as pd 
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
from itertools import product
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, f1_score, recall_score
from sklearn.preprocessing import StandardScaler

## Wczytanie danych

In [5]:
data = pd.read_csv("../data/adult.csv")

## Przykłady z optymalizacji

[Przykłady](https://en.wikipedia.org/wiki/Test_functions_for_optimization) ciekawych funkcji benchmarkowych. Poniżej zostaną przedstawione proste dwie

In [41]:
x = np.linspace(-10, 10, 100)
y = np.linspace(-10, 10, 100)
xv, yv = np.meshgrid(x, y)

In [45]:
def booth_function(xy):
    return np.power((xy[:,0] + 2*xy[:,1] - 7),2) + np.power((2*xy[:,0] + xy[:,1] - 5),2)
def himmelblaus_function(xy):
    return np.power(xy[:,0]**2 + xy[:,1] - 11, 2) + np.power(xy[:,0] + xy[:,1]**2 -7, 2) 

In [220]:
def plot_booth(history = None):
    x = np.linspace(-10, 10, 100)
    y = np.linspace(-10, 10, 100)
    xv, yv = np.meshgrid(x, y)
    vals = booth_function(np.array(list(product(x,y))))
    fig = go.Figure()
    fig.add_trace(go.Scatter3d(x = xv.flatten(), y = yv.flatten(), z = vals, mode='markers', marker=dict(size=2, color=np.log(vals), colorscale='Viridis',)))
    if history is not None:
        fig.add_trace(go.Scatter3d(x = history[:,0], y = history[:,1], z = history[:,2], line=dict(color='darkblue',width=2) ))
    fig.show()
    
def plot_himmelblaus(history = None):
    x = np.linspace(-5, 5, 100)
    y = np.linspace(-5, 5, 100)
    xv, yv = np.meshgrid(x, y)
    vals = himmelblaus_function(np.array(list(product(x,y))))
    fig = go.Figure()
    fig.add_trace(go.Scatter3d(x = xv.flatten(), y = yv.flatten(), z = vals, mode='markers', marker=dict(size=2, color=np.log(vals), colorscale='Viridis',)))
    if history is not None:
        fig.add_trace(go.Scatter3d(x = history[:,0], y = history[:,1], z = history[:,2], line=dict(color='darkblue',width=2) ))
    fig.show()
    

In [215]:
plot_booth()

In [216]:
plot_himmelblaus()

### Definiowanie gradientu
Czyli po prostu policzone pochodne powyższych funkcji

In [217]:
def booth_gradient(x, y):
    return np.array([-34 + 10*x + 8*y, -38 + 8*x + 10*y])

def himmelblaus_gradient(x, y):
    return np.array([2*(-7 + x + y**2 + 2*x*(-11 + x**2 + y)), 2*(-11 + x**2 + y + 2*y*(-7 + x + y**2))])

## Logika stojąca za Gradient Descent

- 1. Posiadaj różniczkowalną funkcje $F$ zależną od $\theta$, mierzącą skutecznośc modelu na danych $X$
- 2. Dla danych $X$ policz gradient funkcji $\frac{d}{d\theta}F$
- 3. Popraw $\theta$ używając gradientu
- 4. Powtarzaj aż osiągniesz ustaloną liczbę iteracji lub nie będzie pomiędzy mini popraw


In [245]:
max_iters = 50
history = []

learning_rate = 0.001

theta  = np.random.uniform(-5,5,2)

for _iter in range(max_iters):
    step = - learning_rate * himmelblaus_gradient(*theta)
    theta +=step
    loss = himmelblaus_function(theta.reshape(1,-1))
    history.append([*theta, loss[0]])
    print(f"{theta[0]:0.2f} {theta[1]:0.2f} ,loss= {loss[0]:0.2f}")

history = np.array(history)

2.34 -4.48 ,loss= 336.95
2.40 -4.18 ,loss= 254.73
2.47 -3.95 ,loss= 200.56
2.53 -3.76 ,loss= 162.34
2.60 -3.59 ,loss= 133.95
2.66 -3.46 ,loss= 112.03
2.73 -3.34 ,loss= 94.60
2.79 -3.23 ,loss= 80.42
2.85 -3.14 ,loss= 68.69
2.91 -3.05 ,loss= 58.86
2.96 -2.98 ,loss= 50.56
3.01 -2.91 ,loss= 43.50
3.06 -2.85 ,loss= 37.48
3.11 -2.79 ,loss= 32.32
3.15 -2.74 ,loss= 27.90
3.19 -2.69 ,loss= 24.11
3.23 -2.65 ,loss= 20.86
3.27 -2.61 ,loss= 18.08
3.30 -2.57 ,loss= 15.69
3.33 -2.53 ,loss= 13.64
3.35 -2.50 ,loss= 11.89
3.38 -2.47 ,loss= 10.38
3.40 -2.44 ,loss= 9.09
3.42 -2.42 ,loss= 7.99
3.44 -2.39 ,loss= 7.03
3.46 -2.37 ,loss= 6.22
3.47 -2.34 ,loss= 5.51
3.49 -2.32 ,loss= 4.90
3.50 -2.30 ,loss= 4.37
3.51 -2.28 ,loss= 3.91
3.52 -2.27 ,loss= 3.51
3.53 -2.25 ,loss= 3.16
3.54 -2.23 ,loss= 2.86
3.55 -2.22 ,loss= 2.59
3.55 -2.20 ,loss= 2.35
3.56 -2.19 ,loss= 2.14
3.56 -2.18 ,loss= 1.95
3.57 -2.17 ,loss= 1.78
3.57 -2.15 ,loss= 1.63
3.57 -2.14 ,loss= 1.50
3.58 -2.13 ,loss= 1.38
3.58 -2.12 ,loss= 1.27
3.58 -

In [246]:
plot_himmelblaus(history)

In [271]:
max_iters = 20
history = []

learning_rate = 0.01

theta  = np.array([-10,-8.0])

for _iter in range(max_iters):
    step = - learning_rate * booth_gradient(*theta)
    theta +=step
    loss = booth_function(theta.reshape(1,-1))
    history.append([*theta, loss[0]])
    print(f"{theta[0]:0.2f} {theta[1]:0.2f} ,loss= {loss[0]:0.2f}")

history = np.array(history)

-8.02 -6.02 ,loss= 1464.49
-6.40 -4.40 ,loss= 984.72
-5.07 -3.07 ,loss= 662.13
-3.97 -1.97 ,loss= 445.21
-3.08 -1.08 ,loss= 299.36
-2.34 -0.34 ,loss= 201.29
-1.74 0.26 ,loss= 135.35
-1.25 0.75 ,loss= 91.01
-0.84 1.16 ,loss= 61.19
-0.51 1.49 ,loss= 41.15
-0.24 1.76 ,loss= 27.67
-0.02 1.98 ,loss= 18.60
0.17 2.17 ,loss= 12.51
0.32 2.32 ,loss= 8.41
0.44 2.44 ,loss= 5.66
0.54 2.54 ,loss= 3.80
0.62 2.62 ,loss= 2.56
0.69 2.69 ,loss= 1.72
0.75 2.75 ,loss= 1.16
0.79 2.79 ,loss= 0.78


In [272]:
plot_booth(history)

### No dobrze ale jako to przełożyć na dane?

In [274]:
data.head()

age  fnlwgt  capital-gain  capital-loss  hours-per-week  \
0   39   77516          2174             0              40   
1   50   83311             0             0              13   
2   38  215646             0             0              40   
3   53  234721             0             0              40   
4   28  338409             0             0              40   

   workclass_Local-gov  workclass_Never-worked  workclass_Private  \
0                    0                       0                  0   
1                    0                       0                  0   
2                    0                       0                  1   
3                    0                       0                  1   
4                    0                       0                  1   

   workclass_Self-emp-inc  workclass_Self-emp-not-inc  ...  race_Black  \
0                       0                           0  ...           0   
1                       0                           1  ...           0   
2                       0                           0  ...           0   
3                       0                           0  ...           1   
4                       0                           0  ...           1   

   race_Other  race_White  sex_Male  native-country_Germany  \
0           0           1         1                       0   
1           0           1         1                       0   
2           0           1         1                       0   
3           0           0         1                       0   
4           0           0         0                       0   

   native-country_Mexico  native-country_Philippines  \
0                      0                           0   
1                      0                           0   
2                      0                           0   
3                      0                           0   
4                      0                           0   

   native-country_United-States  native-country_other  pay_>50K  
0                             1                     0         0  
1                             1                     0         0  
2                             1                     0         0  
3                             1                     0         0  
4                             0                     1         0  

[5 rows x 64 columns]

In [311]:
numeric_columns = ['age','fnlwgt','capital-gain','capital-loss','hours-per-week']
data[numeric_columns] = StandardScaler().fit_transform(data[numeric_columns])

In [312]:
data.shape

(32537, 64)

In [313]:
y = data["pay_>50K"]
X = data.drop("pay_>50K", axis = 1)
X_train_val, X_test, y_train_val, y_test = train_test_split(X, y, random_state=420, test_size=0.2)
X_train, X_val, y_train, y_val = train_test_split(X_train_val, y_train_val, random_state=420, test_size=0.125)

## Loss function (funkcja straty, różnicy) $L(\hat y, y)$
Całkiem dobre [źródło](https://web.stanford.edu/~jurafsky/slp3/5.pdf)

 <h5>$L(\hat y, y)$ = Jak bardzo $\hat y$ różni się od prawdziwego $y$ </h5>


### Loss function dla klasyfikacji binarnej

### Cross-entropy


Wychodzimy od tego, że dla klasyfikacji binarnej chcemy znaleźć takie parametry, które maksymalizują prawdopodobieństwo poprawnego zakwalifikowania próbki $x$. Czyli 

\begin{equation}
\tag{1}
P(y|x) = \hat y^y (1-\hat y)^y
\end{equation}


gdzie jednocześnie $\hat y = f_{\theta}(x)$, a $f$ oznacza nasz model, zależny od wyuczonych parametrów $\theta$ i danych wejściowych $x$

W tym przypadku nasz model będzie bardzo prosty i zdefiniujemy go jako $h_{\theta}$ zdefiniowane poniżej

\begin{equation}
\tag{sigmoid}
h_{\theta}(x) = \frac{1}{1+e^{-\theta^T x}}
\end{equation}

Zauważmy, że funkcja, która maksymalizuje $(1)$ maksymalizuje też logarytm tego wyrażenia. Zdefiniujmy $J(\theta)$ jako naszą funkcję straty, która jest zależna tylko od wyuczonych parametrów modelu.

\begin{align*}
\tag{gradient} 
J(\theta) &= - log(p(y|x)) \\
 & = - log\left(\hat y^y (1-\hat y)^y \right) \\ 
 & = - y \times log(\hat y) + (1-y) \times log(1-\hat y) 
\end{align*}

Ale chcemy obliczyć funkcję różnicy nie tyko dla pojedyńczej próbki, ale dla całego zbioru danych o liczności $m$. Tak więc zsumujemy błędy i uśrednimy je dla wszytskich próbek.

\begin{align*}
\tag{gradient}
J(\theta) = - \frac{1}{m} \sum_{i=1}^{m} \left[ y^{(i)} \times log(h_{\theta}(x^{(i)})) + (1-y^{(i)}) \times log(1-h_{\theta}(x^{(i)})) \right] 
\end{align*}

#### Gradient descent

Pojawia się wtedy gdy policzymy pochodną naszej funkcji różnicy i iteracyjnie poprawiamy parametry modelu $\theta$.
\begin{equation}
\tag{gradient descent}
\theta_j \gets \theta_j - \alpha \frac{\partial}{\partial \theta_j} J(\theta)
\end{equation}
gdzie $j$ oznacza j-ty parametr modelu, a $\alpha$ - learning rate.


#### Gradient funkcji różnicy


\begin{equation}
\frac{\partial}{\partial \theta_j} J(\theta) = \frac{1}{m} \sum_{i=1}^{m} \left( h_{\theta}(x^{(i)}) - y^{(i)} \right) x_j^{(i)}
\end{equation}


#### Ostateczny wzór
Dla tak zdefiniowanego problemu klasyfikacji binarnej, modelu oraz funkcji różnicy ostatecznie otrzymujemy poniższy wzór na iteracyjną poprawę $\theta_j$


\begin{equation}
\tag{3}
\theta_j \gets \theta_j - \alpha \frac{1}{m} \sum_{i=1}^{m} \left( h_{\theta}(x^{(i)}) - y^{(i)} \right) x_j^{(i)}
\end{equation}

In [296]:
def sigmoid(X, theta, eta = 1e-12):
    return 1/ (1 + np.exp(-X.dot(theta.T)+eta))

def calc_loss(X,y,theta, eta = 1e-12):
    return -(np.log(sigmoid(X, theta)+eta).dot(y.T) + np.log(1-sigmoid(X,theta)+eta).dot((1-y).T))/X.shape[0]

def predict(X, theta, threshold = 0.5):
    y_pred_proba = sigmoid(X, theta)
    return (y_pred_proba>threshold)*1

def calc_gradient(X,y,theta):
    return (sigmoid(X,theta) - y).T.dot(X)/X.shape[0]

In [321]:
def GradientDescent(X_train, y_train, learning_rate=0.1, max_iters=50):
    # theta powinna mieć shape (X_train.shape[1],)
    pass

In [322]:
theta = GradientDescent(X_train, y_train)

Iter 000 train_loss = 2.7625, f1_score: 0.3884
Iter 001 train_loss = 2.5956, f1_score: 0.3884
Iter 002 train_loss = 2.4328, f1_score: 0.3884
Iter 003 train_loss = 2.2746, f1_score: 0.3886
Iter 004 train_loss = 2.1220, f1_score: 0.3892
Iter 005 train_loss = 1.9756, f1_score: 0.3903
Iter 006 train_loss = 1.8363, f1_score: 0.3924
Iter 007 train_loss = 1.7047, f1_score: 0.3951
Iter 008 train_loss = 1.5815, f1_score: 0.3987
Iter 009 train_loss = 1.4670, f1_score: 0.4042
Iter 010 train_loss = 1.3616, f1_score: 0.4104
Iter 011 train_loss = 1.2652, f1_score: 0.4173
Iter 012 train_loss = 1.1779, f1_score: 0.4257
Iter 013 train_loss = 1.0993, f1_score: 0.4355
Iter 014 train_loss = 1.0290, f1_score: 0.4457
Iter 015 train_loss = 0.9665, f1_score: 0.4572
Iter 016 train_loss = 0.9112, f1_score: 0.4681
Iter 017 train_loss = 0.8625, f1_score: 0.4795
Iter 018 train_loss = 0.8196, f1_score: 0.4872
Iter 019 train_loss = 0.7820, f1_score: 0.4956
Iter 020 train_loss = 0.7490, f1_score: 0.5024
Iter 021 trai

### Zadanie zaimplementować algorytm Adam
Bardzo ważny algorytm, domyślny wybór w przypadku wielu sieci neuronowych, posiada wiele zalet, jak szybka zbieżność, pozwalająca tanio zweryfikować poprawność architektury.

[źródło](https://arxiv.org/pdf/1412.6980.pdf) wiedzy na temat Adama

In [324]:
def Adam(X_train, y_train, learning_rate=0.1, momentum = 0.9, decay = 0.999, max_iters=50):    
    pass

## Budowanie drzew wzmocnionych gradientowo
### Przypomnienie fragmentu starszych labów


source: [Friedman](https://jerryfriedman.su.domains/ftp/trebst.pdf)

0. Input: training set $\{(x_{i},y_{i})\}_{i=1}^{n}$ a differentiable loss function $L(y,F(x))$ number of iterations M.

Algorithm:

- 1. Initialize model with a constant value:
\begin{equation}
F_0(x) = \underset{\gamma}{\arg\min} \sum_{i=1}^n L(y_i, \gamma)
\end{equation}

- 2. For m = 1 to M:
 - 2.1 Compute so-called pseudo-residuals:
\begin{equation}
r_{im} = -\left[\frac{\partial L(y_i, F(x_i))}{\partial F(x_i)}\right]_{F(x)=F_{m-1}(x)} \quad \mbox{for } i=1,\ldots,n.
\end{equation}

 - 2.2. Fit a base learner (or weak learner, e.g. tree) closed under scaling $h_{m}(x)$ to pseudo-residuals, i.e. train it using the training set $\{(x_i, r_{im})\}_{i=1}^n$
 
 - 2.3. Compute multiplier $\gamma _{m}$ by solving the following one-dimensional optimization problem:
\begin{equation}
\gamma_m = \underset{\gamma}{\operatorname{arg\,min}} \sum_{i=1}^n L\left(y_i, F_{m-1}(x_i) + \gamma h_m(x_i)\right).
\end{equation}

 - 2.4 Update the model:
\begin{equation}
F_{m}(x)=F_{{m-1}}(x)+\nu \gamma _{m}h_{m}(x).
\end{equation}

3. Output $F_M(x)$.


### Okej ale co to w ogóle znaczy?
krok po kroku

### 0.

Dla konkretnego problemu opisanego przez zbiór $\{(x_{i},y_{i})\}_{i=1}^{n}$ wybieramy funkcję $L(y,F(x))$ tzw. *loss*, która opisuje jak dobre jest nasze rozwiązanie.

W naszym przypadku będziemy rozważać $\large L(y,\hat{y}) = \frac{1}{2}(y-\hat{y})^2$

Jest ona zależna od naszej predykcji $F(x)$ oraz oryginalnych danych $y$. Musi być ona różniczkowalna! Określamy również (chociaż nie musimy liczbę drzew, które iteracyjnie chcemy zbudować, domyślnie 100)

### 1. Inicjalizacja
Wyznaczamy początkową predykcję zmiennej celu, która najlepiej na razie przybliża $y$. Domyślnie taką najlepszą predykcją jest średnia

### 2. Iteracyjnie budujemy nowe to drzewa

- ### 2.1
Obliczamy nasz gradient, który tak naprawdę okazuje się być rezyduami.

$ \large \left[\frac{\partial L(y_i, F(x_i))}{\partial F(x_i)}\right] = \frac{\partial}{\partial \hat{y}} L(y,\hat{y}) = \frac{\partial}{\partial \hat{y}} \frac{1}{2}(y-\hat{y})^2 = (y-\hat{y}) = r_{m}$

- ### 2.2 

Dla przekształconego zbioru danych $\{(x_{i},r_{im})\}_{i=1}^{n}$ tworzymy nowe drzewo. Tak naprawdę próbuje ono przewidzieć rezydua poprzedniej predykcji, a nie samego y. (Sumowanie wyników tych drzew da nam dopiero estymacje samego y)

 - ### 2.3

Obliczanie $\gamma_m$ nazywanego inaczej *output value*. Wygląda niebezpiecznie i można wyznaczyć analitycznie poprzez rozwiązanie danego równania, natomiast jest to też średnia wartość rezuduów na danym liściu i z takiej interpretacji będę korzystał.


- ## 2.4
Na koniec poprawiamy naszą predykcję $y$ o wyliczoną gammę najczęściej przemnożoną przez $\nu$, które oznacza po porstu *learning_rate*. Lepiej jest wykonywać drobne kroki do celu niż gwałtowne.

$ \large y_m = y_{{m-1}} + \nu \gamma _{m}h_{m}(x)$


### 3.

Po wykonaniu się liczby iteracji bądź jeżeli został spełniony inny warunek wcześniejszego zatrzymania otrzymujemy ostateczny wynik wraz z zbudowanymi drzewami możliwymi do zastosowania przy predykcji



## Sieci neuronowe

### Convolution Neural Networks (CNNs) - Konwolucyjne sieci neuronowe
[omówienie](https://insightsimaging.springeropen.com/articles/10.1007/s13244-018-0639-9)

### Generative Adversarial Networks (GANs) i Variational Autoencoder (VAE)
 przykład implementacji w [tensorflow](https://www.tensorflow.org/tutorials/generative/dcgan) 
 
 krótkie wyjaśnienie [minmax loss function](https://developers.google.com/machine-learning/gan/loss) dla GANów 

### Deep Reinforcment Learning (RL) - głębokie uczenie ze wzmocnieniem
wideo [przykład](https://www.youtube.com/watch?v=SX08NT55YhA&t=170s) z TrackMani

### Transformers - Transformatory

#### Kamienie milowe Deep NLP
Attention Is All You Need [arxiv](https://arxiv.org/abs/1706.03762)   
An Image is Worth 16x16 Words! [arxiv](https://arxiv.org/abs/2010.11929)

#### Przykłady
GPT-3 - kolosalny model NLP [arxiv](https://arxiv.org/pdf/2005.14165.pdf)

DALL-E 2 - model który rozumie tekst i obrazki [instagram?](https://www.instagram.com/openaidalle/)
